In [1]:
import pandas as pd
import numpy as np
import pickle
import gymnasium as gym
from gymnasium.spaces import Box, Discrete
import statistics
from utils import methods
from utils.rl_environments.env1 import Env1

with open(methods.file_path('prof_data/data1_intervals.pkl', 'data'), 'rb') as f:
    intervals = pickle.load(f)

df = pd.read_csv(methods.file_path('prof_data/data1.csv', 'data'))

df['intervals'] = intervals
display(df.head())

PPO_MODEL = methods.file_path('ppo_env1', 'models')


total  travel_time         h         c  \
0   43.0     3.535281  5.320843  1.787906   
1   48.0    41.459338  0.120220  1.670595   
2   31.0   114.792988  0.146738  6.669483   
3   52.0   976.197274  0.003427  0.570308   
4   39.0    41.909987  0.105977  3.407713   

                                           intervals  
0  [0.1306593104459917, 0.08214531495921755, 0.02...  
1  [4.276706517433805, 3.2544721073860834, 3.7400...  
2  [16.079087401217105, 11.608519241181346, 14.23...  
3  [28.206915811705233, 6.758341759637238, 24.521...  
4  [0.9262261308152662, 1.9254123526889755, 3.236...

In [2]:
from stable_baselines3 import PPO
model = PPO.load(PPO_MODEL)

env = Env1()
rewards = {}
print(env._get_info())
for i in range(len(df)):
    row = df.iloc[i]
    state, _ = env.reset(row=row)
    done = False
    total_reward = 0
    while not done:
        action, _ = model.predict(state)  
        state, reward, done, _, info = env.step(action)
        total_reward += reward
    rewards[i] = total_reward
    # print(f"Episode {i} reward: {total_reward} | h = {info['state']['h']}, c = {info['state']['c']}")
    print(f"Episode {i} reward: {total_reward} | cur_time = {info['state']['cur_time']}")


df['rewards'] = rewards

df.head()

{'hidden': {'alpha': -1, 'beta': -1, 'interval': -1, 'cum_sum_intervals': -1}, 'state': {'n': -1, 'N': -1, 'h': -1, 'c': -1, 'travel_time': -1, 'cur_time': -1, 'mean_n': -1, 'std_n': -1, 'alpha_hat': -1, 'beta_hat': -1, 'u_star_hat': -1, 'last_update': -1}}
Episode 0 reward: -1.7879058522669198 | cur_time = 3.9387106959965377
Episode 1 reward: -16.789159941828782 | cur_time = 12.271261353239975
Episode 2 reward: -42.04328268505151 | cur_time = 42.02336413816172
Episode 3 reward: -0.38013569490368493 | cur_time = 59.586525123710274
Episode 4 reward: -6.789738754827452 | cur_time = 19.688359553252457
Episode 5 reward: -100.69850606104622 | cur_time = 2857.9977671615893
Episode 6 reward: -16.33518834971634 | cur_time = 10.571790100250428
Episode 7 reward: -2.821401950265599 | cur_time = 22.237525017502858
Episode 8 reward: -8.67367327638704 | cur_time = 40.072576122541044
Episode 9 reward: -432.2751247914234 | cur_time = 722.5480170021746
Episode 10 reward: -6.972097527830836 | cur_time =

total  travel_time         h         c  \
0   43.0     3.535281  5.320843  1.787906   
1   48.0    41.459338  0.120220  1.670595   
2   31.0   114.792988  0.146738  6.669483   
3   52.0   976.197274  0.003427  0.570308   
4   39.0    41.909987  0.105977  3.407713   

                                           intervals    rewards  
0  [0.1306593104459917, 0.08214531495921755, 0.02...  -1.787906  
1  [4.276706517433805, 3.2544721073860834, 3.7400... -16.789160  
2  [16.079087401217105, 11.608519241181346, 14.23... -42.043283  
3  [28.206915811705233, 6.758341759637238, 24.521...  -0.380136  
4  [0.9262261308152662, 1.9254123526889755, 3.236...  -6.789739

In [3]:
import plotly.graph_objects as go

# Calculate means
means = df[['rewards', 'h', 'c']].mean()

# Plot
fig = go.Figure(data=[go.Bar(x=means.index, y=means.values)])
fig.update_layout(title="Mean Values of Rewards, H, and C", yaxis_title="Mean Value")
fig.show()

# Calculate medians
medians = df[['rewards', 'h', 'c']].median()

# Plot
fig = go.Figure(data=[go.Bar(x=medians.index, y=medians.values)])
fig.update_layout(title="Median Values of Rewards, H, and C", yaxis_title="Median Value")
fig.show()









In [4]:
# filter total > 30 in df
# df = df[df['total'] > 30]
df['alpha'] = df.apply(lambda row: methods.gamma_estimate_parameters(int(row['total']), row['intervals'])[0], axis=1)
df['beta'] = df.apply(lambda row: methods.gamma_estimate_parameters(int(row['total']), row['intervals'])[1], axis=1)
df['mean'] = df.apply(lambda row: statistics.mean(row['intervals']), axis=1)
df['std'] = df.apply(lambda row: statistics.stdev(row['intervals']), axis=1)

# alpha, beta, h, c scatter plot plotly
fig = go.Figure(data=[go.Scatter(x=df['alpha'], y=df['beta'], mode='markers', marker=dict(size=5))])
fig.update_layout(title="Alpha vs Beta", xaxis_title="Alpha", yaxis_title="Beta")
fig.show()

fig = go.Figure(data=[go.Scatter(x=df['h'], y=df['c'], mode='markers', marker=dict(size=5))])
fig.update_layout(title="H vs C", xaxis_title="H", yaxis_title="C")
fig.show()

fig = go.Figure(data=[go.Scatter(x=df['h'] / df['c'], y= 1 / df['beta'], mode='markers', marker=dict(size=5))])
fig.update_layout(title="h/c vs 1/beta", xaxis_title="h/c", yaxis_title="1/beta")
fig.show()

fig = go.Figure(data=[go.Scatter(x=df['travel_time'], y=df['intervals'].apply(lambda row: sum(row[3:])), mode='markers', marker=dict(size=5))])
fig.update_layout(title="Travel Time vs Total", xaxis_title="Travel Time", yaxis_title="Total")
# add y = x line
fig.add_trace(go.Scatter(x=[0, 10000], y=[0, 10000], mode='lines', name='y=x'))
fig.show()


In [5]:

# I want range of alpha and beta, total, h, c
total_range = (df['total'].min(), df['total'].max())
h_range = (df['h'].min(), df['h'].max())
c_range = (df['c'].min(), df['c'].max())
alpha_range = (df['alpha'].min(), df['alpha'].max())
beta_range = (df['beta'].min(), df['beta'].max())
mean_range = (df['mean'].min(), df['mean'].max())
std_range = (df['std'].min(), df['std'].max())
travel_time_range = (df['travel_time'].min(), df['travel_time'].max())
print(f"Alpha range: {alpha_range}")
print(f"Beta range: {beta_range}")
print(f"Total range: {total_range}")
print(f"H range: {h_range}")
print(f"C range: {c_range}")
print(f"Mean range: {mean_range}")
print(f"Std range: {std_range}")
print(f"Travel time range: {travel_time_range}")
df.head(50)

Alpha range: (0.028460825724258725, 567.9556442351517)
Beta range: (0.0004579081838998966, 32.62570309852111)
Total range: (20.0, 70.0)
H range: (3.556345624867136e-05, 581.5328467536872)
C range: (0.0009908023283743, 48.4727568441552)
Mean range: (0.00018347907565493645, 1255.491447762732)
Std range: (0.0003966596764921248, 123.31431960764903)
Travel time range: (0.0003935176331111, 34658.29848422208)


total   travel_time         h          c  \
0    43.0      3.535281  5.320843   1.787906   
1    48.0     41.459338  0.120220   1.670595   
2    31.0    114.792988  0.146738   6.669483   
3    52.0    976.197274  0.003427   0.570308   
4    39.0     41.909987  0.105977   3.407713   
5    40.0  18968.864118  0.005753   2.546631   
6    37.0      5.713274  3.593902  16.335188   
7    42.0    112.727918  0.152379   4.193468   
8    36.0     24.318587  0.141482   2.120688   
9    49.0   1672.335583  0.051048  14.763162   
10   29.0      0.553074  3.664845   6.972098   
11   29.0     45.935564  0.025994   0.269066   
12   43.0    561.297561  0.046785   6.974101   
13   40.0    236.938279  0.877416  10.282375   
14   39.0     15.054231  0.242116   0.747981   
15   41.0    239.484427  0.076714   3.158692   
16   37.0      3.454190  1.564540   3.872203   
17   33.0      7.605284  0.200966   1.987508   
18   41.0    117.119889  0.000233   0.030613   
19   45.0    143.728310  0.750053  20.169748   
20   39.0     11.285926  0.305859   0.781980   
21   39.0      8.827999  0.803961   4.812354   
22   46.0      1.764111  1.875636   3.233692   
23   49.0    113.580398  0.073664   4.039454   
24   47.0     13.755405  0.328409   4.422927   
25   43.0   3578.209185  0.006350   1.546439   
26   36.0     17.694637  0.214461   1.666056   
27   40.0    104.344403  0.054953   5.052963   
28   41.0      9.951650  0.384565   3.989844   
29   36.0     30.394588  1.536642   6.365424   
30   35.0     26.767184  0.153792   3.456650   
31   59.0     67.336903  0.070388   5.046022   
32   30.0    108.003802  0.071697   3.300172   
33   33.0     24.631067  0.491782   4.846625   
34   37.0    384.864075  0.131437   8.543923   
35   30.0     25.695919  0.009434   0.230758   
36   34.0      7.481168  0.036144   0.539970   
37   33.0   1305.694248  0.003059   0.969607   
38   42.0    616.460023  0.050707   3.400493   
39   40.0    169.051059  0.193413   4.162711   
40   32.0    247.202745  0.014092   0.115077   
41   46.0      0.629506  2.012441   5.413152   
42   38.0      2.283692  3.757627   3.891407   
43   43.0     21.945019  0.345031   4.600025   
44   36.0     25.148466  0.321001   3.936634   
45   37.0      0.719854  1.893374   1.374593   
46   51.0     10.732008  0.400071   1.902928   
47   35.0     12.809439  0.391659   1.959971   
48   45.0    154.503036  0.118645   2.128979   
49   43.0    547.064921  0.005523   0.555012   

                                            intervals     rewards       alpha  \
0   [0.1306593104459917, 0.08214531495921755, 0.02...   -1.787906    2.912900   
1   [4.276706517433805, 3.2544721073860834, 3.7400...  -16.789160   15.414274   
2   [16.079087401217105, 11.608519241181346, 14.23...  -42.043283    4.699589   
3   [28.206915811705233, 6.758341759637238, 24.521...   -0.380136    3.904633   
4   [0.9262261308152662, 1.9254123526889755, 3.236...   -6.789739    2.909377   
5   [964.5425831234778, 845.9818291341096, 1047.37... -100.698506  124.686414   
6   [0.46221294532785073, 0.08902386135418568, 0.0...  -16.335188    0.451451   
7   [9.601735204923799, 2.821560185146939, 9.31422...   -2.821402    1.778240   
8   [16.86292821044016, 1.0866065475530133, 0.8230...   -8.673673    0.836405   
9   [262.7323029378378, 215.39368190149267, 244.32... -432.275125   56.095389   
10  [0.004275479501779492, 0.09375074564332414, 0....   -6.972098    0.835173   
11  [2.8772813907949053, 5.050261950384793, 5.5452...   -0.716856    5.005140   
12  [30.85301313022481, 39.1153219471561, 28.94239...  -36.832813    9.808395   
13  [6.432664982401554, 5.726782782242298, 7.68216...  -14.211761   14.501799   
14  [0.6681966408285855, 0.26685703584232456, 0.47...   -0.747981    2.123627   
15  [7.319718884929741, 5.315211526472114, 1.16533...   -5.305006    3.190811   
16  [0.7830947977590851, 1.0022670644589118, 1.014...   -3.872203   11.372554   
17  [1.295120762657061, 1.0102717052854668, 2.9605...   -1.987508    1.965105   
18  [34.45987870

In [6]:
#plot distribution of alpha, beta, h, c
fig = go.Figure(data=[go.Histogram(x=df['alpha'])])
fig.update_layout(title="Alpha Distribution", xaxis_title="Alpha")
fig.add_vline(x=df['alpha'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['alpha'].mean():.2f}")
fig.show()

fig = go.Figure(data=[go.Histogram(x=df['beta'])])
fig.update_layout(title="Beta Distribution", xaxis_title="Beta")
fig.add_vline(x=df['beta'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['beta'].mean():.2f}")
fig.show()

fig = go.Figure(data=[go.Histogram(x=df['h'])])
fig.update_layout(title="H Distribution", xaxis_title="H")
fig.add_vline(x=df['h'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['h'].mean():.2f}")
fig.show()

fig = go.Figure(data=[go.Histogram(x=df['c'])])
fig.update_layout(title="C Distribution", xaxis_title="C")
fig.add_vline(x=df['c'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['c'].mean():.2f}")
fig.show()

fig = go.Figure(data=[go.Histogram(x=df['total'])])
fig.update_layout(title="Total Distribution", xaxis_title="Total")
fig.add_vline(x=df['total'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['total'].mean():.2f}")
fig.add_vline(x=df['total'].mean() + df['total'].std(), line_dash="dash", line_color="green", annotation_text=f"Std: {df['total'].std():.2f}")
fig.show()

fig = go.Figure(data=[go.Histogram(x=df['travel_time'])])
fig.update_layout(title="Travel Time Distribution", xaxis_title="Travel Time")
fig.add_vline(x=df['travel_time'].mean(), line_dash="dash", line_color="red", annotation_text=f"Mean: {df['travel_time'].mean():.2f}")
fig.show()



In [7]:
from pandarallel import pandarallel

# Initialize pandarallel with progress bar enabled
pandarallel.initialize(progress_bar=True)
for i in [0, 3, 5]:
    print(f"Optimal reward at n = {i}")
    df[f'u{i}'] = df.apply(lambda row: row['intervals'][i:].sum(), axis=1)
    df[f'u_star{i}'] = df.apply(lambda row: (print(row), methods.get_u_star_binary_fast(row['total'] - i, row['alpha'], row['beta'], row['h'], row['c']))[1], axis=1)
    df[f'optimal_rewards{i}'] = df.apply(lambda row: -methods.cal_cost(row['c'], row['h'], row[f'u{i}'], row[f'u_star{i}']), axis=1)

df['direct_leave_rewards'] = df.apply(lambda row: -methods.cal_cost(row['c'], row['h'], row['intervals'][3:].sum(), row[f'travel_time']), axis=1)
df.head()

INFO: Pandarallel will run on 8 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.
Optimal reward at n = 0
total                                                       43.0
travel_time                                             3.535281
h                                                       5.320843
c                                                       1.787906
intervals      [0.1306593104459917, 0.08214531495921755, 0.02...
rewards                                                -1.787906
alpha                                                     2.9129
beta                                                    0.031168
mean                                                    0.090789
std                                                     0.053195
u0                                                      3.903929
Name: 0, dtype: object
total                                                       48.0
trav

TypeError: Invalid NaN comparison

In [ ]:
tp = df[df['h'] / df['c'] >= 1 / df['beta']]
tp.head(14)
# len(tp)

total  travel_time          h          c  \
795    54.0    22.572009   0.306247   1.979096   
814    35.0     1.701905   1.211772   2.074716   
890    44.0     5.918861   2.202298   2.832889   
951    39.0     1.840705   0.760142   2.353463   
1777   27.0     0.905625   0.860297   0.778439   
2338   32.0     0.322215   1.218925   5.743359   
3483   34.0     1.764753   0.488458   0.726780   
5070   32.0     1.082955   0.802421   1.431228   
5400   51.0     1.666707   1.359409   6.937835   
7993   39.0     1.527342   3.818864   3.713327   
8222   38.0     0.854046  10.502926  10.074127   
9376   33.0     3.716964   1.000060   2.252174   
9463   35.0     4.106537   0.696108   1.559691   

                                              intervals    rewards     alpha  \
795   [0.014973814481733946, 0.00025907574946661, 3....  -8.737229  0.109503   
814   [0.4377438803130833, 1.2852740352673644e-05, 0...  -5.837467  0.089269   
890   [7.025081195069271e-11, 0.041764422951962234, ...  -0.518553  0.109002   
951   [1.9270370635383731, 6.182731466592538, 3.4052...  -2.335951  0.101808   
1777  [0.0008414023526065289, 4.2248169348672495e-06...  -0.507997  0.050949   
2338  [0.004318316620975128, 1.0384232836324901e-15,...  -7.959696  0.040331   
3483  [9.871602143827961e-07, 6.211606145992767e-07,...  -0.726780  0.032679   
5070  [0.0001735600897038623, 4.413734654859798, 1.6...  -2.472780  0.129209   
5400  [8.44294861622943e-34, 4.5398285616949235e-05,... -20.930972  0.042002   
7993  [6.003552808625337e-06, 0.0018803849879250453,...  -4.250445  0.066464   
8222  [2.8196937015861276e-07, 4.2165402348264676e-2...  -9.827517  0.028926   
9376  [0.04598641102833948, 1.4113668788782624e-23, ...  -2.608903  0.071499   
9463  [4.137144093967448e-09, 0.8931730920053076, 0....  -5.821602  0.122038   

          beta      mean       std         u0  
795   8.661550  0.948468  2.866217  51.217262  
814   2.297203  0.205068  0.686355   7.177385  
890   1.313322  0.143155  0.433599   6.298818  
951   3.305240  0.336501  1.054616  13.123520  
1777  1.228955  0.062614  0.277399   1.690587  
2338  5.390276  0.217395  1.082505   6.956631  
3483  1.595630  0.052143  0.288446   1.772871  
5070  2.495929  0.322498  0.897180  10.319925  
5400  8.012666  0.336546  1.642143  17.163862  
7993  1.075194  0.071462  0.277192   2.787020  
8222  1.719184  0.049730  0.292395   1.889739  
9376  2.742850  0.196112  0.733421   6.471698  
9463  3.153027  0.384788  1.101475  13.467591

In [ ]:
from utils import math_expressions as me
import numpy as np
from sympy import symbols, erf, pi, sympify, E
row = df.iloc[795]
alpha = row['alpha']
beta = row['beta']
h = row['h']
c = row['c']
total = row['total']
print(row)
h_precise = lambda x: float(me.gamma_hazard_rate((alpha * total), beta).subs(symbols('x'), x).evalf())
x = np.linspace(0, 457, 1000)
print(h_precise(457.4584584584585))
y = [(print(i), h_precise(i))[1] for i in x]
# print y_norm if imaginary
fig = go.Figure(data=[go.Scatter(x=x, y=y)])
fig.update_layout(title="Gamma Hazard Rate", xaxis_title="x", yaxis_title="f(x)")
fig.show()

u = methods.get_u_star_binary_fast(row['total'], row['alpha'], row['beta'], row['h'], row['c'])

total                                                       54.0
travel_time                                            22.572009
h                                                       0.306247
c                                                       1.979096
intervals      [0.014973814481733946, 0.00025907574946661, 3....
rewards                                                -8.645355
alpha                                                   0.109503
beta                                                     8.66155
mean                                                    0.948468
std                                                     2.866217
u0                                                     51.217262
Name: 795, dtype: object
0.01689748031019771
0.0
0.4574574574574575
0.914914914914915
1.3723723723723724
1.82982982982983
2.2872872872872874
2.744744744744745
3.2022022022022023
3.65965965965966
4.117117117117117
4.574574574574575
5.032032032032032
5.48948948948949
5.946946946946947
6

TypeError: Invalid NaN comparison

In [ ]:
from utils import math_expressions as me
import numpy as np
from sympy import symbols, erf, pi, sympify, E



import plotly.graph_objects as go
from scipy.stats import gamma, norm
import time
alpha = 1000
beta = 0.1


h_precise = lambda x: (me.gamma_hazard_rate((alpha), beta).subs(symbols('x'), x).evalf(5))
h_precise2 = lambda x: (me.gamma_hazard_rate((alpha), beta, x).evalf())
pdf = lambda x: gamma.pdf(x, alpha, scale=beta)
cdf = lambda x: gamma.cdf(x, alpha, scale=beta)
h_fast = lambda x: pdf(x) / (1 - cdf(x))
pdf_log = lambda x: gamma.logpdf(x, alpha, scale=beta)
cdf_log = lambda x: gamma.logcdf(x, alpha, scale=beta)

j = 351
print(cdf_log(j), cdf(j), me.gamma_cdf(alpha, beta, j).evalf(40))


x = np.linspace(0, (alpha * beta  + 4 * beta * np.sqrt(alpha)) * 8, 20)
# time y and y2

start_time = time.time()
y = [(print(i), h_precise(i))[1] for i in x]
end_time = time.time()
print(f"Execution time for y2: {end_time - start_time} seconds")


start_time = time.time()
y2 = [(print(i), h_precise2(i))[1] for i in x]
end_time = time.time()
print(f"Execution time for y2: {end_time - start_time} seconds")
print(y)
print(y2)
y_fast = [h_fast(i) for i in x]
y_pdf = [pdf(i) for i in x]
print(y_fast)
# print y_norm if imaginary
fig = go.Figure(data=[go.Scatter(x=x, y=y), go.Scatter(x=x, y=y_fast), go.Scatter(x=x, y=y_pdf)])
fig.update_layout(title="Gamma Hazard Rate", xaxis_title="x", yaxis_title="f(x)")
fig.show()


0.0 1.0 1.000000000000000000000000000000000000000
0.0
47.43120448028358
94.86240896056717
142.29361344085075
189.72481792113433
237.1560224014179
284.5872268817015
332.0184313619851
379.44963584226866
426.8808403225522
474.3120448028358
521.7432492831194
569.174453763403
616.6056582436865
664.0368627239702
711.4680672042538
758.8992716845373
806.3304761648209
853.7616806451044
901.1928851253881
Execution time for y2: 5.805858135223389 seconds
0.0
47.43120448028358
94.86240896056717
142.29361344085075
189.72481792113433
237.1560224014179
284.5872268817015
332.0184313619851
379.44963584226866
426.8808403225522
474.3120448028358
521.7432492831194
569.174453763403
616.6056582436865
664.0368627239702
711.4680672042538
758.8992716845373
806.3304761648209
853.7616806451044
901.1928851253881
Execution time for y2: 3.231959104537964 seconds
[0, 6.1993e-97, 0.035693, 2.9956, 4.7403, 5.7906, 6.4915, 6.9924, 7.3682, 7.6605, 7.8944, 8.0857, 8.2452, 8.3802, 8.4958, 8.5961, 8.6838, 8.7612, 8.8300, 8.

/var/folders/6b/tmvvscrj5wb5r4ngnndf1gtm0000gn/T/ipykernel_33964/581731328.py:18: RuntimeWarning:

divide by zero encountered in scalar divide

/var/folders/6b/tmvvscrj5wb5r4ngnndf1gtm0000gn/T/ipykernel_33964/581731328.py:18: RuntimeWarning:

invalid value encountered in scalar divide



TypeError: Object of type Zero is not JSON serializable

In [ ]:
from utils import methods
alpha = 137.883037
beta = 1.873392
total = 34
h = 0.005466
c = 1.279461
u = methods.get_u_star_binary_fast(total, alpha, beta, h, c)
print(u)


8726.81340929
